![piggy_bank](piggy_bank.jpg)

<br>

Personal loans are a lucrative revenue stream for banks. The typical interest rate of a two year loan in the United Kingdom is [around 10%](https://www.experian.com/blogs/ask-experian/whats-a-good-interest-rate-for-a-personal-loan/). This might not sound like a lot, but in September 2022 alone UK consumers borrowed [around £1.5 billion](https://www.ukfinance.org.uk/system/files/2022-12/Household%20Finance%20Review%202022%20Q3-%20Final.pdf), which would mean approximately £300 million in interest generated by banks over two years!

You have been asked to work with a bank to clean and store the data they collected as part of a recent marketing campaign, which aimed to get customers to take out a personal loan. They plan to conduct more marketing campaigns going forward so would like you to set up a PostgreSQL database to store this campaign's data, designing the schema in a way that would allow data from future campaigns to be easily imported. 

They have supplied you with a csv file called `"bank_marketing.csv"`, which you will need to clean, reformat, and split, in order to save separate files based on the tables you will create. It is recommended to use `pandas` for these tasks.

Lastly, you will write the SQL code that the bank can execute to create the tables and populate with the data from the csv files. As the bank are quite strict about their security, you'll save SQL files as multiline string variables that they can then use to create the database on their end. 

You have been asked to design a database that will have three tables:

## client

| column | data type | description | original column in dataset |
|--------|-----------|-------------|----------------------------|
| `id` | `serial` | Client ID - primary key | `client_id` |
| `age` | `integer` | Client's age in years | `age` |
| `job` | `text` | Client's type of job | `job` |
| `marital` | `text` | Client's marital status | `marital` | 
| `education` | `text` | Client's level of education | `education` |
| `credit_default` | `boolean` | Whether the client's credit is in default | `credit_default` |
| `housing` | `boolean` | Whether the client has an existing housing loan (mortgage) | `housing` | 
| `loan` | `boolean` | Whether the client has an existing personal loan | `loan` |

<br>

## campaign

| column | data type | description | original column in dataset |
|--------|-----------|-------------|----------------------------|
| `campaign_id` | `serial` | Campaign ID - primary key | N/A - new column |
| `client_id` | `serial` | Client ID - references `id` in the `client` table | `client_id` |
| `number_contacts` | `integer` | Number of contact attempts to the client in the current campaign | `campaign` |
| `contact_duration` | `integer` | Last contact duration in seconds | `duration` |
| `pdays` | `integer` | Number of days since contact in previous campaign (`999` = not previously contacted) | `pdays` |
| `previous_campaign_contacts` | `integer` | Number of contact attempts to the client in the previous campaign | `previous` |
| `previous_outcome` | `boolean` | Outcome of the previous campaign | `poutcome` |
| `campaign_outcome` | `boolean` | Outcome of the current campaign | `y` |
| `last_contact_date` | `date` | Last date the client was contacted | A combination of `day`, `month`, and the newly created `year` |

<br>

## economics

| column | data type | description | original column in dataset |
|--------|-----------|-------------|----------------------------|
| `client_id` | `serial` | Client ID - references `id` in the `client` table | `client_id` |
| `emp_var_rate` | `float` | Employment variation rate (quarterly indicator) | `emp_var_rate` |
| `cons_price_idx` | `float` | Consumer price index (monthly indicator) | `cons_price_idx` |
| `euribor_three_months` | `float` | Euro Interbank Offered Rate (euribor) three month rate (daily indicator) | `euribor3m` |
| `number_employed` | `float` | Number of employees (quarterly indicator)| `nr_employed` |

Imported necessary packages

> Instruction 1:
> Read in `bank_marketing.csv`

> Instruction 2:
> Split the data into three DataFrames using information provided about the desired tables as your guide: one with information about the `client`, another containing `campaign` data, and a third to store information about `economics` at the time of the campaign.

- Master DataFrame as `df`
- Split the DataFrame into the specified DataFrames: `client`, `campaign` and `economics`

In [17]:
import pandas as pd
import numpy as np

df = pd.read_csv('bank_marketing.csv')
print(list(df))

client = df[['client_id', 'age', 'job', 'marital', 'education', 'credit_default', 'housing', 'loan']]
campaign = df[['client_id', 'campaign', 'duration', 'duration', 'pdays', 'previous', 'poutcome', 'y', 'day', 'month']]
economics = df[['client_id', 'emp_var_rate', 'cons_price_idx', 'euribor3m', 'nr_employed']]

['client_id', 'age', 'job', 'marital', 'education', 'credit_default', 'housing', 'loan', 'contact', 'month', 'day', 'duration', 'campaign', 'pdays', 'previous', 'poutcome', 'emp_var_rate', 'cons_price_idx', 'cons_conf_idx', 'euribor3m', 'nr_employed', 'y']


> Instruction 3: 
> Rename the column `"client_id"` to `"id"` in `client` (leave as-is in the other subsets);
> `"duration"` to `"contact_duration"`, `"previous"` to `"previous_campaign_contacts"`, `"y"` to `"campaign_outcome"`, `"poutcome"` to `"previous_outcome"`, and `"campaign"` to `"number_contacts"` in `campaign`;
> and `"euribor3m"` to `"euribor_three_months"` and `"nr_employed"` to `"number_employed"` in `economics`.

In [18]:
client = client.rename(columns = {'client_id':'id'})
campaign = campaign.rename(columns = {
    'duration': 'contact_duration',
    'previous': 'previous_campaign_contacts',
    'y' : 'campaign_outcome',
    'poutcome': 'previous_outcome',
    'campaign': 'number_contacts'
})
economics = economics.rename(columns = {
    'euribor3m': 'euribor_three_months',
    'nr_employed': 'number_employed'
})

View the three DataFrames

In [19]:
client

id  age          job  ... credit_default housing loan
0          0   56    housemaid  ...             no      no   no
1          1   57     services  ...        unknown      no   no
2          2   37     services  ...             no     yes   no
3          3   40       admin.  ...             no      no   no
4          4   56     services  ...             no      no  yes
...      ...  ...          ...  ...            ...     ...  ...
41183  41183   73      retired  ...             no     yes   no
41184  41184   46  blue-collar  ...             no      no   no
41185  41185   56      retired  ...             no     yes   no
41186  41186   44   technician  ...             no      no   no
41187  41187   74      retired  ...             no     yes   no

[41188 rows x 8 columns]

In [20]:
campaign

client_id  number_contacts  contact_duration  ...  campaign_outcome  day  month
0              0                1               261  ...                no   13    may
1              1                1               149  ...                no   19    may
2              2                1               226  ...                no   23    may
3              3                1               151  ...                no   27    may
4              4                1               307  ...                no    3    may
...          ...              ...               ...  ...               ...  ...    ...
41183      41183                1               334  ...               yes   30    nov
41184      41184                1               383  ...                no    6    nov
41185      41185                2               189  ...                no   24    nov
41186      41186                1               442  ...               yes   17    nov
41187      41187                3               239  ...                no   23    nov

[41188 rows x 10 columns]

In [21]:
economics

client_id  emp_var_rate  ...  euribor_three_months  number_employed
0              0           1.1  ...                 4.857           5191.0
1              1           1.1  ...                 4.857           5191.0
2              2           1.1  ...                 4.857           5191.0
3              3           1.1  ...                 4.857           5191.0
4              4           1.1  ...                 4.857           5191.0
...          ...           ...  ...                   ...              ...
41183      41183          -1.1  ...                 1.028           4963.6
41184      41184          -1.1  ...                 1.028           4963.6
41185      41185          -1.1  ...                 1.028           4963.6
41186      41186          -1.1  ...                 1.028           4963.6
41187      41187          -1.1  ...                 1.028           4963.6

[41188 rows x 5 columns]

> Instruction 3:
> Clean the `"education"` column, changing `"."` to `"_"` and `"unknown"` to NumPy's null values.

> Instruction 4: 
> Remove periods from the `"job"` column.

> Instruction 5:
> Convert `"success"` and `"failure"` in the `"previous_outcome"` and `"campaign_outcome"` columns to binary (`1` or `0`), along with the changing `"nonexistent"` to NumPy's null values in `"previous_outcome"`.

> Instruction 6: 
> Add a column called `campaign_id` in `campaign`, where all rows have a value of `1`.

In [22]:
# Education column
client['education'] = client['education'].apply(lambda x: x.replace('.', '_'))
client['education'].replace('unknown', np.nan, inplace=True)

# Job column
client['job'] = client['job'].apply(lambda x: x.replace('.', ''))

# Campaign outcomes
outcome_map = {'success': 1, 'failure': 0, 'non_existent': np.nan, 'yes': 1, 'no': 0}
campaign['previous_outcome'] = campaign['previous_outcome'].map(outcome_map)
campaign['campaign_outcome'] = campaign['campaign_outcome'].map(outcome_map)

# Add column campaign_id into campaign
campaign['campaign_id'] = 1

In [23]:
client

id  age          job  ... credit_default housing loan
0          0   56    housemaid  ...             no      no   no
1          1   57     services  ...        unknown      no   no
2          2   37     services  ...             no     yes   no
3          3   40        admin  ...             no      no   no
4          4   56     services  ...             no      no  yes
...      ...  ...          ...  ...            ...     ...  ...
41183  41183   73      retired  ...             no     yes   no
41184  41184   46  blue-collar  ...             no      no   no
41185  41185   56      retired  ...             no     yes   no
41186  41186   44   technician  ...             no      no   no
41187  41187   74      retired  ...             no     yes   no

[41188 rows x 8 columns]

In [24]:
campaign

client_id  number_contacts  contact_duration  ...  day  month  campaign_id
0              0                1               261  ...   13    may            1
1              1                1               149  ...   19    may            1
2              2                1               226  ...   23    may            1
3              3                1               151  ...   27    may            1
4              4                1               307  ...    3    may            1
...          ...              ...               ...  ...  ...    ...          ...
41183      41183                1               334  ...   30    nov            1
41184      41184                1               383  ...    6    nov            1
41185      41185                2               189  ...   24    nov            1
41186      41186                1               442  ...   17    nov            1
41187      41187                3               239  ...   23    nov            1

[41188 rows x 11 columns]

> Instruction 7: 
> Create a `datetime` column called `last_contact_date`, in the format of `"year-month-day"`, where the year is `2022`, and the month and day values are taken from the `"month"` and `"day"` columns.

In [25]:
# Create late_contact_date of type datetime
campaign['year'] = 2022
campaign['last_contact_date'] = pd.to_datetime(
    campaign['year'].astype(str) + '-' +
    campaign['month'].astype(str) + '-' +
    campaign['day'].astype(str),
    errors='coerce'
)

> Instruction 8:
> Remove any redundant data that might have been used to create new columns, ensuring the columns in each subset of the data match the table displayed in the notebook.

In [26]:
campaign = campaign.drop(['day', 'month', 'year'], axis = 1)
campaign

client_id  number_contacts  ...  campaign_id  last_contact_date
0              0                1  ...            1         2022-05-13
1              1                1  ...            1         2022-05-19
2              2                1  ...            1         2022-05-23
3              3                1  ...            1         2022-05-27
4              4                1  ...            1         2022-05-03
...          ...              ...  ...          ...                ...
41183      41183                1  ...            1         2022-11-30
41184      41184                1  ...            1         2022-11-06
41185      41185                2  ...            1         2022-11-24
41186      41186                1  ...            1         2022-11-17
41187      41187                3  ...            1         2022-11-23

[41188 rows x 10 columns]

> Instruction 9: 
> Save the three DataFrames to csv files without an index as `client.csv`, `campaign.csv`, and `economics.csv` respectively.

In [27]:
client.to_csv('client.csv', index=False)
campaign.to_csv('campaign.csv', index=False)
economics.to_csv('economics.csv', index=False)

> Instruction 10-12: 
> - Create a Python variable called `client_table`, containing SQL code as a multi-line string to create a table called `client` using values from client.csv.
> - Create a Python variable called `campaign_table`, containing SQL code as a multi-line string to create a table called `campaign` using values from campaign.csv.
> - Create a Python variable called `economics_table`, containing SQL code as a multi-line string to create a table called `economics` using values from economics.csv

> Instruction 13: 
> In client, campaign, and economic, ensure the final line copies the data from their respective csv files using the following template code snippet: 
> <br> 
> `\copy table_name from 'file_name.csv' DELIMITER ',' CSV HEADER`

In [28]:
client_table = '''
CREATE TABLE client (
    id SERIAL PRIMARY KEY, 
    age INT,
    job TEXT,
    marital TEXT,
    education TEXT,
    credit_default BOOLEAN,
    housing BOOLEAN,
    loan BOOLEAN
);

\copy client from 'client.csv' DELIMITER ',' CSV HEADER
'''

campaign_table = '''
CREATE TABLE campaign (
    campaign_id SERIAL PRIMARY KEY,
    client_id SERIAL REFERENCES client (id),
    number_contacts INT,
    contact_duration INT,
    pdays INT,
    previous_campaign_contacts INT,
    previous_outcome BOOLEAN,
    campaign_outcome BOOLEAN,
    last_contact_date DATE
);

\copy campaign from 'campaign.csv' DELIMITER ',' CSV HEADER
'''

economics_table = '''
CREATE TABLE economics (
    client_id SERIAL REFERENCES client (id),
    emp_var_rate FLOAT,
    cons_price_idx FLOAT,
    euribor_three_months FLOAT,
    number_employed FLOAT
);

\copy economics from 'economics.csv' DELIMITER ',' CSV HEADER
'''

# End of project!